# check dataset: MQ2008
- MQ2008: https://www.microsoft.com/en-us/research/project/letor-learning-rank-information-retrieval/letor-4-0/

In [1]:
%load_ext autoreload

In [2]:
%autoreload 2

import pathlib

from typing import Any

import pandas as pd
import numpy as np
import lightgbm as lgb
import optuna
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_slice

from dataset import mq2008, prepare_lightgbm_dataset
from eval import calc_ndgc_by_model, calc_ndgc

/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Dataset: MQ2008

In [3]:
src_path = pathlib.Path("~/Documents/data/MQ2008/Fold1").expanduser()
assert src_path.exists()

dst_path = pathlib.Path("./data/mq2008").resolve()
for dir_path in [*dst_path.parents[::-1], dst_path]:
    if not dir_path.exists():
        dir_path.mkdir()
assert dst_path.exists()

In [4]:
mq2008(src_path, dst_path)

----------------------------------
Characteristics of dataset mq2008 train
rows x columns (9630, 46)
sparsity: 47.22673709874035
y distribution
Counter({0.0: 7820, 1.0: 1223, 2.0: 587})
num samples in queries: minimum, median, maximum
5 8.0 121
----------------------------------
----------------------------------
Characteristics of dataset mq2008 test
rows x columns (2874, 46)
sparsity: 46.112825633112465
y distribution
Counter({0.0: 2319, 1.0: 378, 2.0: 177})
num samples in queries: minimum, median, maximum
6 14.5 119
----------------------------------


## Model: LightGBM LambdaMART

In [5]:
(
    (dtrain, df_train, X_train, y_train, q_train),
    (dval, df_val, X_val, y_val, q_val),
    (dtest, df_test, X_test, y_test, q_test),
) = prepare_lightgbm_dataset(dst_path)

In [6]:
from typing import Optional

def get_params(trial: Optional[optuna.Trial] = None, study: Optional[optuna.Study] = None):
    base_params = {
        # for model
        "boosting_type": "gbdt",
        "objective": "lambdarank",
        "label_gain": "0,1,2",
        # to avoid overfitting
        "learning_rate":0.1,
        "num_boost_round":10000,
        "num_leaves":31,
        "max_depth":-1,
        "min_split_gain":0.0,
        "min_child_weight":0.001,
        "min_child_samples":20,
        "reg_alpha":0.0,
        "reg_lambda":0.0,
        # to speed up
        "subsample":1.0,
        "subsample_freq":0,
        "colsample_bytree":1.0,
        # https://robotenique.github.io/posts/gbm-histogram/
        "subsample_for_bin":200000,
        # for eval
        "metric": "ndcg",
        "eval_at": "10",
        # misc
        "random_state":1026,
        "n_jobs":-1,
        "saved_feature_importance_type": 0,
        # https://lightgbm.readthedocs.io/en/latest/Advanced-Topics.html#missing-value-handle
        # https://github.com/microsoft/LightGBM/issues/2921
        "use_missing":True,
    }

    if trial is not None:
        search_params = {
            "learning_rate":trial.suggest_float("learning_rate", 1e-3, 1e-1, log=True),
            "num_leaves":trial.suggest_int("num_leaves", 2, 2**8),
            "max_depth":trial.suggest_int("max_depth", 2, 2**8),
            "reg_alpha":trial.suggest_float("reg_alpha", 1e-1, 1e+2, log=True),
            "reg_lambda":trial.suggest_float("reg_lambda", 1e-1, 1e+2, log=True),
            "subsample":trial.suggest_float("subsample", 0.1, 1.0),
            "subsample_freq":1,
            "colsample_bytree":trial.suggest_float("colsample_bytree", 0.1, 1.0),
        }
        base_params.update(search_params)
    if study is not None:
        base_params.update(study.best_params)

    return base_params


In [7]:
import numpy.typing as npt
from functools import partial


def objective(
    trial: optuna.Trial,
    dtrain: lgb.Dataset,
    dval: lgb.Dataset,
    X_val: npt.NDArray[np.float64],
    y_val: npt.NDArray[np.float64],
    q_val: npt.NDArray[np.int64],
):
    params = get_params(trial)
    pruning_callback = optuna.integration.LightGBMPruningCallback(
        trial, "ndcg@10", valid_name="val"
    )
    early_stopping_callback = lgb.early_stopping(stopping_rounds=10)
    model = lgb.train(
        params=params,
        train_set=dtrain,
        valid_sets=[dval],
        valid_names=["val"],
        callbacks=[early_stopping_callback, pruning_callback],
        early_stopping_rounds=10,
    )

    ndgc = calc_ndgc_by_model(model, X_val, y_val, q_val)
    return ndgc


In [8]:
partial_objective = partial(
    objective, dtrain=dtrain, dval=dval, X_val=X_val, y_val=y_val, q_val=q_val
)
study = optuna.create_study(
    direction="maximize",
    sampler=optuna.samplers.TPESampler(seed=1026),
    pruner=optuna.pruners.MedianPruner(n_startup_trials=10, n_warmup_steps=10),
)
study.optimize(partial_objective, n_trials=1000, timeout=600)


[I 2023-06-18 21:36:04,619] A new study created in memory with name: no-name-e13070f0-519d-48b7-8c60-fe4cfbf293b0
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:177: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2023-06-18 21:36:04,948] Trial 0 finished with value: 0.5335552154779474 and parameters: {'learning_rate': 0.00505002891383059, 'num_leaves': 216, 'max_depth': 245, 'reg_alpha': 0.362855527267345, 'reg_lambda': 1.4805565704

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006887 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:177: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2023-06-18 21:36:05,143] Trial 1 finished with value: 0.5177770518596084 and parameters: {'learning_rate': 0.0014626593581236452, 'num_leaves': 12, 'max_depth': 217, 'reg_alpha': 0.27312312582311504, 'reg_lambda': 4.134009138426728, 'subsample': 0.4302494542283414, 'colsample_bytree': 0.6887172209709429}. Best is trial 0 with value: 0.

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005106 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[2]	val's ndcg@10: 0.734045
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007290 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning

[I 2023-06-18 21:36:05,299] Trial 2 finished with value: 0.5251992956538712 and parameters: {'learning_rate': 0.06583433918136197, 'num_leaves': 195, 'max_depth': 161, 'reg_alpha': 9.154413372482265, 'reg_lambda': 0.2909666874675726, 'subsample': 0.36745888396421467, 'colsample_bytree': 0.7382377125075835}. Best is trial 0 with value: 0.5335552154779474.
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:177: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future releas

...

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006472 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2023-06-18 21:40:30,668] Trial 998 finished with value: 0.5305993166111387 and parameters: {'learning_rate': 0.0357359253442988, 'num_leaves': 230, 'max_depth': 80, 'reg_alpha': 5.911396679978938, 'reg_lambda': 2.2444350380360905, 'subsample': 0.7716193461634493, 'colsample_bytree': 0.26993725924618417}. Best is trial 365 with value: 0.5519400509532082.


[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005843 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:177: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  _log_warning(f"Found `{alias}` in params. Will use it instead of argument")
/Users/yohei/Documents/tutorial/lambdamart/.venv/lib/python3.11/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2023-06-18 21:40:30,953] Trial 999 pruned. Trial was pruned at iteration 10.


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002807 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

In [9]:
study.best_trial

FrozenTrial(number=365, state=1, values=[0.5519400509532082], datetime_start=datetime.datetime(2023, 6, 18, 21, 37, 40, 155257), datetime_complete=datetime.datetime(2023, 6, 18, 21, 37, 40, 426012), params={'learning_rate': 0.019511265803046518, 'num_leaves': 109, 'max_depth': 93, 'reg_alpha': 4.827032183082831, 'reg_lambda': 2.7503515997825048, 'subsample': 0.9068739334051251, 'colsample_bytree': 0.21053867533080237}, user_attrs={}, system_attrs={}, intermediate_values={0: 0.6434841962951986, 1: 0.7412145123251644, 2: 0.7572546723714335, 3: 0.755431077880156, 4: 0.7594846878535966, 5: 0.7613502374354837, 6: 0.7607450718314029, 7: 0.763438705498083, 8: 0.759495834696203, 9: 0.764940296397665, 10: 0.7670818046865041, 11: 0.7591594095685374, 12: 0.7670148279179497, 13: 0.77006760683384, 14: 0.7668423569261431, 15: 0.7669997105523774, 16: 0.7730191790946782, 17: 0.7643285220109072, 18: 0.7682138707082623, 19: 0.7613005752095658, 20: 0.7662053534864595, 21: 0.7655981834646228, 22: 0.762204

In [10]:
params = get_params(study=study)
early_stopping_callback = lgb.early_stopping(stopping_rounds=10)
log_evaluation_callback = lgb.log_evaluation(period=10)
model = lgb.train(
    params=params,
    train_set=dtrain,
    valid_sets=[dval],
    valid_names=["val"],
    callbacks=[early_stopping_callback, log_evaluation_callback],
    early_stopping_rounds=10,
)

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010037 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9204
[LightGBM] [Info] Number of data points in the train set: 7555, number of used features: 40
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

In [11]:
print(calc_ndgc_by_model(model, X_train, y_train, q_train, k=10))
print(calc_ndgc_by_model(model, X_val, y_val, q_val, k=10))
print(calc_ndgc_by_model(model, X_test, y_test, q_test, k=10))

0.5704432451906072
0.5322959738454996
0.49568343242792334


In [12]:
# random
score = np.random.rand(len(X_test))
calc_ndgc(score, y_test, q_test, k=10)

0.32561153228103795

In [13]:
# best
score = y_test
calc_ndgc(score, y_test, q_test, k=10)

0.6730769230769231

## Check params

In [14]:
study.best_params

{'learning_rate': 0.019511265803046518,
 'num_leaves': 109,
 'max_depth': 93,
 'reg_alpha': 4.827032183082831,
 'reg_lambda': 2.7503515997825048,
 'subsample': 0.9068739334051251,
 'colsample_bytree': 0.21053867533080237}

In [15]:
plot_optimization_history(study)

In [16]:
plot_intermediate_values(study)

In [17]:
plot_param_importances(study)

In [18]:
plot_slice(study, params=["reg_alpha", "num_leaves"])

In [19]:
plot_contour(study, params=["reg_alpha", "num_leaves"])


In [20]:
plot_param_importances(
    study, target=lambda t: t.duration.total_seconds(), target_name="duration"
)
